In [1]:
#####2 goals
"""1)  create the final datajoint tables to store the final spine meshs in:
    a. One table to store the segment data (linked to the components table)
    b. One table to store the labeled mesh vertices and faces of the neurons (linked to CleanseMesh)
2) Create the function that goes through and writes the CGAL library for all of the components
"""

'1)  create the final datajoint tables to store the final spine meshs in:\n    a. One table to store the segment data (linked to the components table)\n    b. One table to store the labeled mesh vertices and faces of the neurons (linked to CleanseMesh)\n2) Create the function that goes through and writes the CGAL library for all of the components\n'

In [2]:
"""Pseduo code for function that goes through and writes the CGAL library for all of the components

1) Recieve list of neurons to do and a flag that when set will look to
    another table for the clustering parameter for each neuron
2) Pull down the neurons mesh data from cleansedMesh
3) Pull down all the components with the neuron ID that have size > 100
4) For each component:
5) Generate the off file:
    ---------------Way I do it in the blender file----------------
    In load_Neuron_automatic_spine, download whole mesh
    a. Before create the mesh object send faces and verts to filter_verts_and_faces
    b. filter_verts_and_faces:
        downloads the indexes for the compartment
        Only saves off the verts that are mentioned in the indexes
        Only saves off the faces that are mentioned in the indexes
            returns them
    c. builds the off file by:
        Finding the faces that have all indices included in the verts list
        finish with the write_Part_Neuron_Off_file
    -------------------
    1. create the file name string: "neuron_" + str(segment_id) + "_" + str(compartment_type_name) + "_" + str(found_component_index)
    2. get the number of indices and faces
    3. Open them and write them to the file
    4. For the vertices:
        For each index in the vertices blob of the components table, 
         write the coordinates in the index location of the Cleansed mesh table
            while creating a lookup dictionary where it has old_vert_index:new_index  (vert_lookup)
    5. For the faces:
        For each index in the faces blob of the components table,
             Get the new index by (vert_lookup) and save to list
        Write the list to the file
    
    Call the CGAL function to generate the labels
    String calculat the CGAL file name and the CGAL SDF value 
    Write the two lists to the datajoint table (linked to components)
    """





'Pseduo code for function that goes through and writes the CGAL library for all of the components\n\n1) Recieve list of neurons to do and a flag that when set will look to\n    another table for the clustering parameter for each neuron\n2) Pull down the neurons mesh data from cleansedMesh\n3) Pull down all the components with the neuron ID that have size > 100\n4) For each component:\n5) Generate the off file:\n    ---------------Way I do it in the blender file----------------\n    In load_Neuron_automatic_spine, download whole mesh\n    a. Before create the mesh object send faces and verts to filter_verts_and_faces\n    b. filter_verts_and_faces:\n        downloads the indexes for the compartment\n        Only saves off the verts that are mentioned in the indexes\n        Only saves off the faces that are mentioned in the indexes\n            returns them\n    c. builds the off file by:\n        Finding the faces that have all indices included in the verts list\n        finish with th

In [3]:
import datajoint as dj
import numpy as np
import datetime
import math

#from cloudvolume import CloudVolume
#from collections import Counter
#from funconnect import ta3

In [4]:
#setting the address and the username
dj.config['database.host'] = '10.28.0.34'
dj.config['database.user'] = 'celiib'
dj.config['database.password'] = 'newceliipass'
dj.config['safemode']=True
dj.config["display.limit"] = 400


# user: celiib
# pass: newceliipass
# host: at-database.ad.bcm.edu
# schemas: microns_% and celiib_%

In [5]:
schema = dj.schema('microns_ta3p100')
ta3p100 = dj.create_virtual_module('ta3p100', 'microns_ta3p100')

Connecting celiib@10.28.0.34:3306


In [7]:
#if temp folder doesn't exist then create it
import os
if (os.path.isdir(os.getcwd() + "/temp")) == False:
    os.mkdir("temp")

In [8]:
import os
import pathlib

def generate_component_off_file(neuron_ID, compartment_type, component_id, n_vertex_indices, n_triangle_indices, 
                                vertex_indices, triangle_indices,vertices, triangles):
    
    #get the current file location
    file_loc = pathlib.Path.cwd() / "temp"
    filename = "neuron_" + str(neuron_ID) + "_" + str(compartment_type) + "_" + str(component_id)
    path_and_filename = file_loc / filename
    
    #open the file and start writing to it    
    f = open(str(path_and_filename) + ".off", "w")
    f.write("OFF\n")
    f.write(str(n_vertex_indices) + " " + str(n_triangle_indices) + " 0\n" )
    
    #start writing all of the vertices
    """
        4. For the vertices:
        For each index in the vertices blob of the components table, 
         write the coordinates in the index location of the Cleansed mesh table
            while creating a lookup dictionary where it has old_vert_index:new_index  (vert_lookup)
    """       
    verts_lookup = {}
    for i, vin in enumerate(vertex_indices):
        #get the coordinates of the vertex
        coordinates = vertices[vin]
        #write the coordinates to the off file
        f.write(str(coordinates[0]) + " " + str(coordinates[1]) + " " + str(coordinates[2])+"\n")
        #create lookup dictionary for vertices
        verts_lookup[vin] = i
    
    """    5. For the faces:
        For each index in the faces blob of the components table,
             Get the new index by (vert_lookup) and save to list
        Write the list to the file"""
    for i,fac in enumerate(triangle_indices):
        verts_in_fac = triangles[fac]
        #write the verties to the off file
        f.write("3 " + str(verts_lookup[verts_in_fac[0]]) + " " + str(verts_lookup[verts_in_fac[1]]) + " " + str(verts_lookup[verts_in_fac[2]])+"\n")
        
    
    print("Done making OFF file " + str(filename))
    #return the name of the off file you created and the location
    return str(path_and_filename),str(filename)

In [9]:
#get the neuron names from the component table


In [31]:
#################THE ONE WE ARE USING
import cgal_Segmentation_Module as csm
import csv
import decimal
import time
import os

@schema
class ComponentAutoSegment(dj.Computed):
    definition = """
    # creates the labels for the mesh table
    -> ta3p100.Compartment.Component
    clusters     : tinyint unsigned  #what the clustering parameter was set to
    smoothness   : decimal(3,2)             #what the smoothness parameter was set to, number betwee 0 and 1
    ---
    n_triangles  : int unsigned # number of faces
    seg_group    : longblob     # group segmentation ID's for faces from automatic CGAL segmentation
    sdf          : longblob     #  width values for faces from from automatic CGAL segmentation
    median_sdf   : decimal(6,5) # the median width value for the sdf values
    mean_sdf     : decimal(6,5) #the mean width value for the sdf values
    third_q      : decimal(6,5) #the upper quartile for the mean width values
    ninety_perc  : decimal(6,5) #the 90th percentile for the mean width values
    time_updated : timestamp    # the time at which the segmentation was performed
   """
    
    key_source = ta3p100.Compartment.Component & 'n_triangle_indices>100' & [dict(compartment_type=comp) for comp in ['Basal', 'Apical', 'Oblique', 'Dendrite']]
    
    whole_neuron_dicts = dict()
    
    def make(self, key):
        print("key = " + str(key))
        #key passed to function is just dictionary with the following attributes
        """segmentation
        segment_id
        decimation_ratio
        compartment_type
        component_index
        """
        start_time = time.time()
        
        #clusters_default = 18
        smoothness = 0.04

        Apical_Basal_Oblique_default = [12]
        basal_big = [16]

        neuron_ID = key["segment_id"]
        component = (ta3p100.Compartment.Component & key).fetch1()        

        component_id = component["component_index"]
        compartment_type = component["compartment_type"]
        component_size = int(component["n_triangle_indices"])

        print("component_size = " + str(component_size))

        if (compartment_type == "Basal") & (component_size > 160000):
            cluster_list = basal_big
        else:
            cluster_list = Apical_Basal_Oblique_default


        for clusters in cluster_list:
            smoothness = 0.04
            print(str(component["segment_id"]) + " type:" + str(component["compartment_type"]) 
                      + " index:" + str(component["component_index"]) + " cluster:" + str(clusters) 
                  + " smoothness:" + str(smoothness))

            #generate the off file for each component
            #what need to send them:
            """----From cleansed Mesh---
            vertices
            triangles
            ----From component table--
            n_vertex_indices
            n_triangle_indices
            vertex_indices
            triangle_indices"""
            
            if key['segment_id'] not in self.whole_neuron_dicts:
                self.whole_neuron_dicts[key['segment_id']] = (ta3p100.CleansedMesh & 'decimation_ratio=0.35' & dict(segment_id=key['segment_id'])).fetch1()
            
            path_and_filename, off_file_name = generate_component_off_file(neuron_ID, compartment_type, component_id,
                                        component["n_vertex_indices"],
                                        component["n_triangle_indices"],
                                        component["vertex_indices"],
                                        component["triangle_indices"],
                                        self.whole_neuron_dicts[key['segment_id']]["vertices"],
                                        self.whole_neuron_dicts[key['segment_id']]["triangles"])
            
            print(len(component['vertex_indices']), len(component['triangle_indices']))
            
            #will have generated the component file by now so now need to run the segmentation
            csm.cgal_segmentation(path_and_filename,clusters,smoothness)

            #generate the name of the files
            cgal_file_name = path_and_filename + "-cgal_" + str(clusters) + "_"+str(smoothness)
            group_csv_cgal_file = cgal_file_name + ".csv"
            sdf_csv_file_name = cgal_file_name+"_sdf.csv"


            with open(group_csv_cgal_file) as f:
              reader = csv.reader(f)
              your_list = list(reader)
            group_list = []
            for item in your_list:
                group_list.append(int(item[0]))

            with open(sdf_csv_file_name) as f:
              reader = csv.reader(f)
              your_list = list(reader)
            sdf_list = []
            for item in your_list:
                sdf_list.append(float(item[0]))

            #print(group_list)
            #print(sdf_list)

            #now write them to the datajoint table  
            #table columns for ComponentAutoSegmentation: segmentation, segment_id, decimation_ratio, compartment_type, component_index, seg_group, sdf
            print(dict(key,
                                clusters=clusters,
                                smoothness=smoothness,
                                n_triangles=component["n_triangle_indices"],
                                seg_group=group_list,
                                sdf=sdf_list,
                                median_sdf=np.median(sdf_list),
                                mean_sdf=np.mean(sdf_list),
                                third_q=np.percentile(sdf_list, 75),
                                ninety_perc=np.percentile(sdf_list, 90),
                                time_updated=str(datetime.datetime.now())[0:19]))
            
            comp_dict = dict(key,
                                clusters=clusters,
                                smoothness=smoothness,
                                n_triangles=component["n_triangle_indices"],
                                seg_group=group_list,
                                sdf=sdf_list,
                                median_sdf=np.median(sdf_list),
                                mean_sdf=np.mean(sdf_list),
                                third_q=np.percentile(sdf_list, 75),
                                ninety_perc=np.percentile(sdf_list, 90),
                                time_updated=str(datetime.datetime.now())[0:19])

            self.insert1(comp_dict)

            #then go and erase all of the files used: the sdf files, 
            real_off_file_name = path_and_filename + ".off"

            files_to_delete = [group_csv_cgal_file,sdf_csv_file_name,real_off_file_name]
            for fl in files_to_delete:
                if os.path.exists(fl):
                    os.remove(fl)
                else:
                    print(fl + " file does not exist")

        print("finished")
        print("--- %s seconds ---" % (time.time() - start_time))

In [34]:
%debug

> /usr/local/lib/python3.6/dist-packages/pymysql/err.py(109)raise_mysql_exception()
    105         errval = data[9:].decode('utf-8', 'replace')
    106     else:
    107         errval = data[3:].decode('utf-8', 'replace')
    108     errorclass = error_map.get(errno, InternalError)
--> 109     raise errorclass(errno, errval)



ipdb>  dir()


['data', 'errno', 'errorclass', 'errval', 'is_41']


ipdb>  data


b'\xff\xac\x05#23000Cannot add or update a child row: a foreign key constraint fails (`microns_ta3p100`.`__component_auto_segment`, CONSTRAINT `__component_auto_segment_ibfk_1` FOREIGN KEY (`segmentation`, `segment_id`, `decimation_ratio`, `compartment_type`, `component_index`))'


...

ipdb>  self.heading


# creates the labels for the mesh table
segmentation         : smallint                     # segmentation id
segment_id           : bigint                       # segment id unique within each Segmentation
decimation_ratio     : decimal(3,2)                 # intended ratio of vertices and faces left after decimation
compartment_type     : varchar(16)                  # Basal, Apical, spine head, etc.
component_index      : smallint unsigned            # Which sub-compartment of a certain label this is.
clusters             : tinyint unsigned             # what the clustering parameter was set to
smoothness           : decimal(3,2)                 # what the smoothness parameter was set to, number betwee 0 and 1
---
n_triangles          : int unsigned                 # number of faces
seg_group            : longblob                     # group segmentation ID's for faces from automatic CGAL segmentation
sdf                  : longblob                     # width values for faces from 

ipdb>  comp_dict.keys()


dict_keys(['segmentation', 'segment_id', 'decimation_ratio', 'compartment_type', 'component_index', 'clusters', 'smoothness', 'n_triangles', 'seg_group', 'sdf', 'median_sdf', 'mean_sdf', 'third_q', 'ninety_perc', 'time_updated'])


ipdb>  q


In [32]:
ComponentAutoSegment.populate(reserve_jobs=True)

key = {'segmentation': 2, 'segment_id': 648518346341366885, 'decimation_ratio': Decimal('0.35'), 'compartment_type': 'Oblique', 'component_index': 0}
component_size = 180622
648518346341366885 type:Oblique index:0 cluster:12 smoothness:0.04
Done making OFF file neuron_648518346341366885_Oblique_0
90569 180622
{'segmentation': 2, 'segment_id': 648518346341366885, 'decimation_ratio': Decimal('0.35'), 'compartment_type': 'Oblique', 'component_index': 0, 'clusters': 12, 'smoothness': 0.04, 'n_triangles': 180622, 'seg_group': [1408, 2638, 2638, 2723, 2723, 2723, 1752, 1752, 1752, 2723, 1408, 452, 2638, 2638, 2152, 2638, 2723, 1752, 1752, 1408, 1408, 2638, 2638, 1408, 1408, 1408, 2373, 2373, 1752, 963, 2638, 1408, 1408, 1752, 2638, 2638, 2638, 2638, 2638, 1408, 1408, 1408, 2560, 2638, 2638, 2638, 1752, 1752, 2560, 1408, 1408, 2638, 663, 663, 1752, 1408, 2638, 2638, 1752, 1752, 2638, 2560, 2560, 663, 1102, 2373, 2638, 2638, 2723, 663, 1447, 1408, 1408, 1408, 1408, 2723, 2723, 2723, 2638, 2638

IntegrityError: (1452, 'Cannot add or update a child row: a foreign key constraint fails (`microns_ta3p100`.`__component_auto_segment`, CONSTRAINT `__component_auto_segment_ibfk_1` FOREIGN KEY (`segmentation`, `segment_id`, `decimation_ratio`, `compartment_type`, `component_index`))')

In [26]:
ta3p100.ComponentAutoSegment().describe()

# creates the labels for the mesh table
-> `microns_ta3`.`__compartment__component`
clusters             : tinyint unsigned             # what the clustering parameter was set to
smoothness           : decimal(3,2)                 # what the smoothness parameter was set to, number betwee 0 and 1
---
n_triangles          : int unsigned                 # number of faces
seg_group            : longblob                     # group segmentation ID's for faces from automatic CGAL segmentation
sdf                  : longblob                     # width values for faces from from automatic CGAL segmentation
median_sdf           : decimal(6,5)                 # the median width value for the sdf values
mean_sdf             : decimal(6,5)                 # the mean width value for the sdf values
third_q              : decimal(6,5)                 # the upper quartile for the mean width values
ninety_perc          : decimal(6,5)                 # the 90th percentile for the mean width values
time

"# creates the labels for the mesh table\n-> `microns_ta3`.`__compartment__component`\nclusters             : tinyint unsigned             # what the clustering parameter was set to\nsmoothness           : decimal(3,2)                 # what the smoothness parameter was set to, number betwee 0 and 1\n---\nn_triangles          : int unsigned                 # number of faces\nseg_group            : longblob                     # group segmentation ID's for faces from automatic CGAL segmentation\nsdf                  : longblob                     # width values for faces from from automatic CGAL segmentation\nmedian_sdf           : decimal(6,5)                 # the median width value for the sdf values\nmean_sdf             : decimal(6,5)                 # the mean width value for the sdf values\nthird_q              : decimal(6,5)                 # the upper quartile for the mean width values\nninety_perc          : decimal(6,5)                 # the 90th percentile for the mean width

In [28]:
new_dict = {'segmentation': 2, 'segment_id': 648518346341366885, 'compartment_type': 'Basal', 'component_index': 3}
ta3p100.Compartment.Component & new_dict







*segmentation  *segment_id    *decimation_ra *compartment_t *component_ind n_vertex_indic n_triangle_ind vertex_ind triangle_i
+------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +--------+ +--------+
2              64851834634136 0.35           Basal          3              276            539            =BLOB=     =BLOB=    
 (1 tuples)

In [33]:
schema.jobs

*table_name    *key_hash      status       key        error_message  error_stac user           host           pid        connection_id  timestamp     
+------------+ +------------+ +----------+ +--------+ +------------+ +--------+ +------------+ +------------+ +--------+ +------------+ +------------+
__component_au 1af3e481683eda error        =BLOB=     IntegrityError =BLOB=     celiib@10.28.2 824ecdc46f17   27         2475015        2019-01-26 20:
__component_au 6365f8e6310787 error        =BLOB=     TypeError: pri =BLOB=     celiib@10.28.2 824ecdc46f17   27         2475015        2019-01-26 19:
__component_au 7419c7cc5ec002 error        =BLOB=     IntegrityError =BLOB=     celiib@10.28.2 824ecdc46f17   27         2475015        2019-01-26 19:
__component_au b9b615180c7a10 error        =BLOB=     IntegrityError =BLOB=     celiib@10.28.2 824ecdc46f17   27         2475015        2019-01-26 19:
__component_au c4bce795221e7a error        =BLOB=     IntegrityError =BLOB=     celiib@10.28.2 824ecdc46f17   27         2475015        2019-01-26 19:
__decimation   3f6d204420095d reserved     =BLOB=                    =BLOB=     jcotton@10.28. at-compute004  188200     1958721        2019-01-10 21:
__decimation   7b1feda329b852 reserved     =BLOB=                    =BLOB=     jcotton@10.28. at-compute004  186672     1958694        2019-01-10 21:
 (7 tuples)